# 训练instance segmentation模型

In [4]:
from ultralytics import YOLO

# ==== 你需要手动填写的列表 ====
yamlFileNames = [  # 数据集 yaml 文件名（不要写后缀 .yaml）
    # "data_split_0.4_0.3_0.3",
    # "data_split_0.5_0.2_0.3",
    "data_split_0.5_0.3_0.2",
    "data_split_0.6_0.2_0.2",
    # "data_split_0.8_0.2_0",
]
batchSizes = [
    # 4, 
    8, 16, 32, 
    # 64,
]
# models = [
#     # "yolo11n-seg.pt",
#     "yolo11s-seg.pt",
#     "yolo11n.pt",
#     "yolo11s.pt",
#     "yolo11m-seg.pt",
#     "yolo11m.pt",
#     # "yolo11l-seg.pt", "yolo11x-seg.pt",
#     # "yolo11l.pt", "yolo11x.pt",
# ]
models = [
    "yolo11n-seg.pt",
    "/workspace/_ty/models/runs_yolov11/output_16mp/good/yolo11m-seg.pt---data_split_0.6_0.2_0.2_8-----0.909/weights/best.pt",
    "/workspace/_ty/models/runs_yolov11/output_16mp/good/yolo11n-seg.pt---data_split_0.6_0.2_0.2_4---0.913/weights/best.pt",
    "/workspace/_ty/models/runs_yolov11/output_16mp/good/yolo11n.pt---data_split_0.6_0.1_0.3_4----0.906/weights/best.pt",
]
# =================================

runPath = "/workspace/_ty/models/runs_yolov11/yaml/"

# 循环遍历
for yamlFileName in yamlFileNames:
    yamlPath = runPath + yamlFileName + ".yaml"
    for modelFile in models:
        for batch in batchSizes:
            print(f"\n🚀 Training model={modelFile}, dataset={yamlFileName}, batch={batch}")

            model = YOLO(modelFile)

            try:
                model.train(
                    data=yamlPath,
                    epochs=1000,
                    imgsz=640,
                    batch=batch,
                    device=0,
                    workers=4,
                    project=f"output/{modelFile}",   # 输出目录
                    name=f"{yamlFileName}_{batch}",  # run 名字更清晰
                )

                # 测试集验证
                model.val(
                    data=yamlPath,
                    split="test",
                    name=f"{yamlFileName}_{batch}_test"
                )
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"⚠️  跳过: model={modelFile}, yaml={yamlFileName}, batch={batch} —— 显存不足")
                    continue
                else:
                    raise  # 不是 OOM 的错误则继续抛出


🚀 Training model=yolo11n-seg.pt, dataset=data_split_0.5_0.3_0.2, batch=8
New https://pypi.org/project/ultralytics/8.3.221 available 😃 Update with 'pip install -U ultralytics'
Ultralytics 8.3.178 🚀 Python-3.11.13 torch-2.8.0+cu128 CUDA:0 (NVIDIA GeForce RTX 5080, 15818MiB)
engine/trainer: agnostic_nms=False, amp=True, augment=False, auto_augment=randaugment, batch=8, bgr=0.0, box=7.5, cache=False, cfg=None, classes=None, close_mosaic=10, cls=0.5, conf=None, copy_paste=0.0, copy_paste_mode=flip, cos_lr=False, cutmix=0.0, data=/workspace/_ty/models/runs_yolov11/yaml/data_split_0.5_0.3_0.2.yaml, degrees=0.0, deterministic=True, device=0, dfl=1.5, dnn=False, dropout=0.0, dynamic=False, embed=None, epochs=1000, erasing=0.4, exist_ok=False, fliplr=0.5, flipud=0.0, format=torchscript, fraction=1.0, freeze=None, half=False, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, imgsz=640, int8=False, iou=0.7, keras=False, kobj=1.0, line_width=None, lr0=0.01, lrf=0.01, mask_ratio=4, max_det=300, mixup=0.0, mode=tr

train: Scanning /workspace/_ty/models/runs_yolov11/data/data_split_0.5_0.3_0.2/train/labels.cache... 37 images, 0 backgrounds, 0 corrupt: 100%|██████████| 37/37 [00:00<?, ?it/s]


val: Fast image access ✅ (ping: 0.1±0.0 ms, read: 1118.2±815.6 MB/s, size: 420.0 KB)


val: Scanning /workspace/_ty/models/runs_yolov11/data/data_split_0.5_0.3_0.2/val/labels.cache... 22 images, 0 backgrounds, 0 corrupt: 100%|██████████| 22/22 [00:00<?, ?it/s]


Plotting labels to output/yolo11n-seg.pt/data_split_0.5_0.3_0.2_8/labels.jpg... 
optimizer: 'optimizer=auto' found, ignoring 'lr0=0.01' and 'momentum=0.937' and determining best 'optimizer', 'lr0' and 'momentum' automatically... 
optimizer: AdamW(lr=0.002, momentum=0.9) with parameter groups 90 weight(decay=0.0), 101 weight(decay=0.0005), 100 bias(decay=0.0)
Image sizes 640 train, 640 val
Using 4 dataloader workers
Logging results to output/yolo11n-seg.pt/data_split_0.5_0.3_0.2_8
Starting training for 1000 epochs...

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


...


229 epochs completed in 0.021 hours.
Optimizer stripped from output/workspace/_ty/models/runs_yolov11/output_16mp/good/yolo11n.pt---data_split_0.6_0.1_0.3_4----0.906/weights/best.pt/data_split_0.6_0.2_0.2_32/weights/last.pt, 5.5MB
Optimizer stripped from output/workspace/_ty/models/runs_yolov11/output_16mp/good/yolo11n.pt---data_split_0.6_0.1_0.3_4----0.906/weights/best.pt/data_split_0.6_0.2_0.2_32/weights/best.pt, 5.5MB

Validating output/workspace/_ty/models/runs_yolov11/output_16mp/good/yolo11n.pt---data_split_0.6_0.1_0.3_4----0.906/weights/best.pt/data_split_0.6_0.2_0.2_32/weights/best.pt...
Ultralytics 8.3.178 🚀 Python-3.11.13 torch-2.8.0+cu128 CUDA:0 (NVIDIA GeForce RTX 5080, 15818MiB)
YOLO11n summary (fused): 100 layers, 2,582,347 parameters, 0 gradients, 6.3 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 1/1 [00:00<00:00, 41.92it/s]


                   all         15         15      0.959          1      0.995      0.743
Speed: 0.1ms preprocess, 0.4ms inference, 0.0ms loss, 0.3ms postprocess per image
Results saved to output/workspace/_ty/models/runs_yolov11/output_16mp/good/yolo11n.pt---data_split_0.6_0.1_0.3_4----0.906/weights/best.pt/data_split_0.6_0.2_0.2_32
Ultralytics 8.3.178 🚀 Python-3.11.13 torch-2.8.0+cu128 CUDA:0 (NVIDIA GeForce RTX 5080, 15818MiB)
YOLO11n summary (fused): 100 layers, 2,582,347 parameters, 0 gradients, 6.3 GFLOPs
val: Fast image access ✅ (ping: 0.1±0.0 ms, read: 1920.5±881.9 MB/s, size: 489.6 KB)


val: Scanning /workspace/_ty/models/runs_yolov11/data/data_split_0.6_0.2_0.2/test/labels.cache... 15 images, 0 backgrounds, 0 corrupt: 100%|██████████| 15/15 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 1/1 [00:00<00:00,  4.39it/s]


                   all         15         15      0.932      0.919      0.965      0.683
Speed: 0.1ms preprocess, 0.7ms inference, 0.0ms loss, 0.4ms postprocess per image
Results saved to output/workspace/_ty/models/runs_yolov11/output_16mp/good/yolo11n.pt---data_split_0.6_0.1_0.3_4----0.906/weights/best.pt/data_split_0.6_0.2_0.2_32_test


# 单个例子

In [9]:
# runPath = "/workspace/models/runs_yolov11/yaml/"
# yamlFileName = "data_split_v1_0.5_0.2_0.3"
# yamlPath = runPath + yamlFileName + ".yaml"

In [10]:
# from ultralytics import YOLO
#
# runPath = "/workspace/models/runs_yolov11/"
# yamlFileName = "data_split_v1_0.5_0.2_0.3"
# yamlPath = runPath + yamlFileName + ".yaml"
#
# model = YOLO("yolo11n-seg.pt")  # load a pretrained model (recommended for training)
#
# # Train the model
# model.train(
#     data=yamlPath,  # 数据路径（文件夹结构符合分类任务格式）
#     epochs=1000,                   # 训练轮数
#     imgsz=640,                   # 输入图像大小
#     batch=64,                    # 批大小
#     device=0,                    # GPU ID
#     workers=4,                    # DataLoader 线程数
#     project="output/runs_yolo11n-seg_batch64",
#     name=yamlFileName
# )
# model.val(data=yamlPath, split="test", name=yamlFileName+"_test")

In [ ]:
from ultralytics import YOLO
# model = YOLO("/workspace/models/runs_yolov11/output/yolo11m-seg.pt/data_split_0.6_0.2_0.2_8-----0.909/weights/best.pt")  # load a pretrained model (recommended for training)
model = YOLO("/workspace/models/runs_yolov11/output/good/yolo11n-seg.pt---data_split_0.6_0.2_0.2_4---0.913/weights/best.pt")  # load a pretrained model (recommended for training)

model.val(data="/workspace/models/runs_yolov11/yaml/data_split_0.6_0.2_0.2.yaml", split="test")